## My First Cycle Rep
Getting an early cycle rep!!!

The parameters are mostly arbitrary, and this isn't final in any way, but it's cool.

#### Preliminaries
The network threshold is 10x what Jingyi suggests in her paper.

In [1]:
# load some packages
import Gavin.utils.make_network as mn
import plotly.graph_objects as go
from time import time
import networkx as nx
import pandas as pd
import oatpy as oat
import numpy as np

# config
DATA_PATH = 'datasets/concept_network/'
# CONCEPT_FILE = 'articles_category_for_2l_abstracts_concepts_processed_v1_EX_102.csv.gz' # Applied Mathematics
CONCEPT_FILE = 'concepts_Applied Economics_1402.csv.gz' # Applied Econ
article_concept_df = mn.filter_article_concept_file(
        DATA_PATH+CONCEPT_FILE,
        relevance_cutoff=0.7,
        min_article_freq=0.0006, # 0.006%
        max_article_freq=0.005, # 0.05%
        normalize_year=True,
        year_min=1920
    ) # use a filtered data file

#### Problem Setup
Take the concept-article dataframe and turn it into a network, then a distance matrix.

In [3]:
G = mn.gen_concept_network(article_concept_df) # make the graph
adj = nx.adjacency_matrix(G, weight='norm_year') # adjacency matrix
node_births = np.array(list(nx.get_node_attributes(G, 'norm_year').values())) # node orgin years, these break the cycle reps (idk why)
adj.setdiag(node_births)
adj = adj.sorted_indices()

#### Homology Calculation
We setup and calculate homology, then do some basic visualizations.

In [4]:
start = time()

# setup the problem
factored = oat.rust.FactoredBoundaryMatrixVr( # two functions that do this, idk what the other one is
        dissimilarity_matrix=adj,
        homology_dimension_max=2
    )

# solve homology
homology = factored.homology( # solve homology
        return_cycle_representatives=True, # These need to be true to be able to make a barcode, makes the problem take ~30% longer (1:30ish)
        return_bounding_chains=True
    )

f'Homology calculation took {time() - start} secs'

'Homology calculation took 491.5531060695648 secs'

In [5]:
# persistance diagram
fig = oat.plot.pd(homology)
fig.update_layout(
        width=600, 
        height=500,
        margin=dict(l=20, r=20, t=20, b=20)
    )
fig.show()

In [6]:
# Barcode diagram
fig = oat.plot.barcode(homology)
fig.update_layout(
        width=1000, 
        height=500,
        margin=dict(l=20, r=20, t=20, b=20)
    )
fig.show()

#### Cycle Rep
Find a cycle rep!

In [ ]:
homology[homology['dimension'] == 1]

dimension     birth     death birth simplex    death simplex  \
id                                                                   
339           1  0.930693  0.950495     [59, 431]    [59, 69, 431]   
340           1  0.920792  0.950495    [162, 618]  [162, 190, 618]   
341           1  0.920792  0.940594     [59, 236]    [35, 59, 236]   
342           1  0.910891  0.930693    [162, 619]  [162, 174, 619]   
343           1  0.910891  0.930693    [150, 585]  [131, 150, 585]   
...         ...       ...       ...           ...              ...   
1811          1  0.475248  0.653465    [442, 450]  [147, 234, 507]   
1812          1  0.475248  0.653465    [304, 693]  [415, 518, 657]   
1813          1  0.475248  0.841584    [244, 667]  [130, 237, 346]   
1814          1  0.475248  0.485149    [140, 153]  [140, 147, 153]   
1815          1  0.465347  0.663366    [155, 508]  [383, 508, 566]   

                                   cycle representative  cycle nnz  \
id                                                                   
339         simplex  filtration coefficient
0   [59,...          9   
340          simplex  filtration coefficient
0   [16...         11   
341         simplex  filtration coefficient
0   [59,...          8   
342          simplex  filtration coefficient
0   [16...         13   
343          simplex  filtration coefficient
0   [15...         16   
...                                                 ...        ...   
1811        simplex  filtration coefficient
0  [442,...          9   
1812        simplex  filtration coefficient
0  [304,...          9   
1813        simplex  filtration coefficient
0  [244,...          5   
1814        simplex  filtration coefficient
0  [140,...          5   
1815        simplex  filtration coefficient
0  [155,...          4   

                                         bounding chain  bounding nnz  
id                                                                     
339              simplex  filtration coefficient
0  ...         494.0  
340                simplex  filtration coefficient
0...         327.0  
341                simplex  filtration coefficient
0...         146.0  
342                simplex  filtration coefficient
0...         230.0  
343                simplex  filtration coefficient
0...         357.0  
...                                                 ...           ...  
1811              simplex  filtration coefficient
0 ...          41.0  
1812              simplex  filtration coefficient
0 ...          37.0  
1813               simplex  filtration coefficient
0...         171.0  
1814             simplex  filtration coefficient
0  ...           3.0  
1815              simplex  filtration coefficient
0 ...          24.0  

[1477 rows x 9 columns]

In [8]:
## Representative Cycle
index_in_homology = 800 # i think this is a cool one

# optimization problem
start = time()
optimal = factored.optimize_cycle(
        birth_simplex=homology['birth simplex'][index_in_homology], 
        problem_type='preserve PH basis'
    )
print(f'Optimizaiton took {time() - start} secs')

dirty_optimal = optimal.loc['optimal cycle', 'chain'] # round all the dumb and bad coefficicents
clean_optimal = dirty_optimal[round(dirty_optimal['coefficient'].astype(float)) != 0]
print(f'Removing {len(dirty_optimal)-len(clean_optimal)}/{len(dirty_optimal)} degenerate simplexes, {len(clean_optimal)} simplicies left')

# rep_cycle_nodes = list(np.array(G.nodes)[pd.to_numeric(clean_optimal['simplex'].explode().drop_duplicates()).tolist()])

unordered_edges = clean_optimal['simplex'].tolist()
rep_cycle_nodes = [unordered_edges.pop()[1]]
while len(unordered_edges) > 0:
    n = rep_cycle_nodes[-1]
    for e in unordered_edges:
        if n in e:
            break
    if e[-1] == n:
        e.reverse()
    rep_cycle_nodes.append(e[1])
    unordered_edges.remove(e)
rep_cycle_nodes = list(np.array(G.nodes)[rep_cycle_nodes])

rep_cycle_nodes


Finished construcing L1 optimization program.
Constraint matrix has 69203 nonzero entries.
Passing program to solver.

Done solving.
MINILP solution: Solution { direction: Minimize, num_vars: 14272, num_constraints: 14880, objective: 2.2772277227735236 }
Optimizaiton took 45.98624396324158 secs
Removing 1842/1846 degenerate simplexes, 4 simplicies left


['south africa', 'food security', 'asian country', 'economic history']

In [ ]:
# Representative bounding chain
start = time()
optimal = factored.optimize_bounding_chain(
        birth_simplex=homology['birth simplex'][index_in_homology], 
    )
print(f'Optimizaiton took {time() - start} secs')

if optimal is None:
    bounding_chain_nodes = []
else:
    dirty_optimal = optimal.loc['optimal bounding chain', 'chain']
    clean_optimal = dirty_optimal[round(dirty_optimal['coefficient'].astype(float)) != 0]
    print(f'Removing {len(dirty_optimal)-len(clean_optimal)}/{len(dirty_optimal)} degenerate simplexes, {len(clean_optimal)} simplicies left')

    bounding_chain_tris = [list(np.array(G.nodes)[tri]) for tri in clean_optimal['simplex']]
    bounding_chain_nodes = list(np.array(G.nodes)[pd.to_numeric(clean_optimal['simplex'].explode().drop_duplicates()).tolist()])
bounding_chain_nodes


Finished construcing L1 optimization program.
Constraint matrix has 60477 nonzero entries.
Passing program to solver.
Optimizaiton took 45.08154296875 secs
Removing 3323/3347 degenerate simplexes, 24 simplicies left

Done solving.
MINILP solution: Solution { direction: Minimize, num_vars: 9137, num_constraints: 10906, objective: 15.237623762796943 }
max difference in boundaries: Some(Ratio { numer: 833520795313905837, denom: 833520795313875328 })


['labor force',
 'manufacture sector',
 'public policy',
 'labor productivity',
 'economic policy',
 'input output model',
 'relative price',
 'exchange rate policy',
 'distribution of income',
 'productivity growth',
 'term of trade',
 'latin american country',
 'european country',
 'foreign trade',
 'capita income',
 'economic reform']

#### Visualizer
Create a visualization of the hole and how it closes using the cycle rep and bounding chain.

In [ ]:
# params
np.random.seed(10)
MIN_YEAR = 1920
MAX_YEAR = 2021
denorm_year = lambda ny: min(MAX_YEAR+1, np.int64(ny * (MAX_YEAR-MIN_YEAR) + MIN_YEAR))

diff_nodes = list(set(bounding_chain_nodes) - set(rep_cycle_nodes)) # nodes not in cycle that help close it
cycle_G = G.subgraph(set(bounding_chain_nodes + rep_cycle_nodes)) # graph of all nodes in the cycle

# birth = denorm_year(homology.loc[i, 'birth']) # animate between birth and death
birth = min(nx.get_node_attributes(cycle_G, 'year').values())-1
death = denorm_year(homology.loc[index_in_homology, 'death'])

theta = np.linspace(0, 2*np.pi, len(rep_cycle_nodes)+1)[:-1]
x = np.cos(theta)
y = np.sin(theta)

pos = dict()
for i, n in enumerate(rep_cycle_nodes):
    pos[n] = np.array([x[i], y[i]])
for n in diff_nodes:
    pos[n] = np.random.normal(0, 0.01, size=2)
if len(diff_nodes) > 0:
    pos = nx.spring_layout(cycle_G, k=2/np.sqrt(len(bounding_chain_nodes)), pos=pos, fixed=rep_cycle_nodes)

def viz_graph(G, yr):
    # triangle locations
    t_x = [] # triangle x
    t_y = [] # triangle y
    for t in bounding_chain_tris:
        t_yr = max([cycle_G.edges[e]['year'] for e in zip(t, t[1:]+[t[0]])]) # year triangle exists
        # we offset one list and pair everything up. Then find the year for each pair of edges and get the max
        if t_yr <= yr:
            a, b, c = t # triangle nodes
            a_x, a_y = pos[a] # a position
            b_x, b_y = pos[b] # b position
            c_x, c_y = pos[c] # c position
            t_x += [a_x, b_x, c_x, a_x, None]
            t_y += [a_y, b_y, c_y, a_y, None]

    tri_trace = go.Scatter(
            x=t_x, y=t_y,
            hoverinfo='none',
            mode='none',
            fill='toself',
            fillcolor='gray',
            opacity=0.25
        )

    # edge locations
    e_x = [] # edge x
    e_y = [] # edge y
    for e in G.edges:
        if cycle_G.edges[e]['year'] <= yr:
            u, v = e # edge goes from u to v
            u_x, u_y = pos[u] # u position
            v_x, v_y = pos[v] # v position
            e_x += [u_x, v_x, None]
            e_y += [u_y, v_y, None]

    edge_trace = go.Scatter(
            x=e_x, y=e_y,
            hoverinfo='none',
            mode='lines',
            line=dict(width=5, color='#888')
        )

    # node locations
    n_x = [] # node x
    n_y = [] # node y
    n_t = [] # node text
    for n in G.nodes:
        if cycle_G.nodes[n]['year'] <= yr:
            x, y = pos[n]
            n_x.append(x)
            n_y.append(y)
            n_t.append(n.title())
        
    node_trace = go.Scatter(
            x=n_x, y=n_y,
            hoverinfo='none',
            mode='markers+text',
            text=n_t,
            marker=dict(
                    size=25,
                    line_width=2
                )
        )
    
    return tri_trace, edge_trace, node_trace

# Add traces
frames = []
for yr in range(birth, death+1):
    tri_trace, edge_trace, node_trace = viz_graph(cycle_G, yr) # viz objects

    # add as frame
    frames.append(go.Frame(
            data=[tri_trace, edge_trace, node_trace],
            name=yr
        ))
    if yr == birth:
        tri_0_trace, edge_0_trace, node_0_trace = tri_trace, edge_trace, node_trace

# create figure
fig = go.Figure(data=[tri_0_trace, edge_0_trace, node_0_trace], frames=frames)

## the rest is coped from the plotly documentation example on mri volume slices
def frame_args(duration):
    return {
            'frame': {'duration': duration},
            'mode': 'immediate',
            'fromcurrent': True,
            'transition': {'duration': 0, 'easing': 'linear'},
        }
fig.update_layout(
        showlegend=False,
        width=500, 
        height=550,
        margin=dict(l=20, r=20, t=20, b=20),
        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False, range=[1.2*min([x[0] for x in pos.values()]), 1.2*max([x[0] for x in pos.values()])]),
        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False, range=[1.2*min([x[1] for x in pos.values()]), 1.2*max([x[1] for x in pos.values()])]),
        updatemenus = [dict(
                buttons=[
                        dict(
                                args=[None, frame_args(200)],
                                label='&#9654;', # play symbol
                                method='animate'
                            ),
                        dict(
                                args=[None, frame_args(0)],
                                label='&#9724;', # play symbol
                                method='animate'
                            )
                    ],
                direction='left',
                pad=dict(l=0, r=0, t=10, b=10),
                type='buttons',
                x=0.1,
                y=0
            )],
        sliders=[
                dict(
                        pad=dict(l=15, r=0, t=10, b=10),
                        len=0.9,
                        x=0.1,
                        y=0,
                        steps=[dict(
                                args=[[f.name], frame_args(0)],
                                label=f.name,
                                method='animate'
                            ) for f in fig.frames],
                    )
            ]
)
fig.show()